In [16]:
import requests

from bs4 import BeautifulSoup
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from sklearn.cluster import KMeans 
import seaborn as sns 
import json 
import matplotlib.cm as cm
import matplotlib.colors as colors
print('library imported')

library imported


In [81]:
!pip install --upgrade pip geopy
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values
from geopy.geocoders import Nominatim 
from pandas.io.json import json_normalize
print('library imported')

    100% |████████████████████████████████| 1.3MB 11.9MB/s 
Requirement already up-to-date: geopy in ./common/.virtualenv/python3/lib/python3.5/site-packages (1.17.0)
  Found existing installation: pip 18.0
    Uninstalling pip-18.0:
      Successfully uninstalled pip-18.0
library imported


In [82]:
!pip install --upgrade pip folium # Standard way

import folium 

print('library imported')

Requirement already up-to-date: pip in ./common/.virtualenv/python3/lib/python3.5/site-packages (18.1)
Requirement already up-to-date: folium in ./common/.virtualenv/python3/lib/python3.5/site-packages (0.6.0)
library imported


In [88]:
url=requests.get('https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M').text #URL
soup=BeautifulSoup(url,'lxml') 
table = soup.find("table",{"class":"wikitable sortable"}) #table Class
text_data = [] #declare List for storage text from table  
text_sys = table.findAll('tr') #detect all <tr> syntax include text

for text_loop in text_sys:
    ex_text = text_loop.findChildren(recursive=False) #explode list from text_sys 
    text_store = [] #declare list for store string text as list
    for read in ex_text:   #2nd loop in ex_text
        text_index = read.text.strip() #arrange text and strip
        text_store.append(text_index) #combine 3-text string as list  
            
    text_data.append(text_store) #out of 2nd loop save whole list text to one variable list 
text_data #try print out data

[['Postcode', 'Borough', 'Neighbourhood'],
 ['M1A', 'Not assigned', 'Not assigned'],
 ['M2A', 'Not assigned', 'Not assigned'],
 ['M3A', 'North York', 'Parkwoods'],
 ['M4A', 'North York', 'Victoria Village'],
 ['M5A', 'Downtown Toronto', 'Harbourfront'],
 ['M5A', 'Downtown Toronto', 'Regent Park'],
 ['M6A', 'North York', 'Lawrence Heights'],
 ['M6A', 'North York', 'Lawrence Manor'],
 ['M7A', "Queen's Park", 'Not assigned'],
 ['M8A', 'Not assigned', 'Not assigned'],
 ['M9A', 'Etobicoke', 'Islington Avenue'],
 ['M1B', 'Scarborough', 'Rouge'],
 ['M1B', 'Scarborough', 'Malvern'],
 ['M2B', 'Not assigned', 'Not assigned'],
 ['M3B', 'North York', 'Don Mills North'],
 ['M4B', 'East York', 'Woodbine Gardens'],
 ['M4B', 'East York', 'Parkview Hill'],
 ['M5B', 'Downtown Toronto', 'Ryerson'],
 ['M5B', 'Downtown Toronto', 'Garden District'],
 ['M6B', 'North York', 'Glencairn'],
 ['M7B', 'Not assigned', 'Not assigned'],
 ['M8B', 'Not assigned', 'Not assigned'],
 ['M9B', 'Etobicoke', 'Cloverdale'],
 [

In [90]:
df=pd.DataFrame(text_data,columns=["Postcode","Borough","Neighbourhood"]) #Assign data to dataframe
df.head()

Postcode       Borough     Neighbourhood
0  Postcode       Borough     Neighbourhood
1       M1A  Not assigned      Not assigned
2       M2A  Not assigned      Not assigned
3       M3A    North York         Parkwoods
4       M4A    North York  Victoria Village

In [91]:
#If Neighbour index have "Not assigned" it will instead a index of Borough.
df.loc[df.Neighbourhood=="Not assigned","Neighbourhood"] = df.Borough 
df.drop(df[df.Borough == 'Borough'].index, inplace=True) #remove name column in index
df.drop(df[df.Borough == 'Not assigned'].index, inplace=True) #remove Borough rows if index =="Not assigned"
df.head()

Postcode           Borough     Neighbourhood
3      M3A        North York         Parkwoods
4      M4A        North York  Victoria Village
5      M5A  Downtown Toronto      Harbourfront
6      M5A  Downtown Toronto       Regent Park
7      M6A        North York  Lawrence Heights

In [68]:
#sort dataframe 
df_ = df.sort_values(by=['Postcode'])
df_.reset_index(inplace=True)
df_.drop('index',axis=1,inplace=True)
df_.head()

Postcode      Borough   Neighbourhood
0      M1B  Scarborough           Rouge
1      M1B  Scarborough         Malvern
2      M1C  Scarborough      Port Union
3      M1C  Scarborough      Rouge Hill
4      M1C  Scarborough  Highland Creek

In [92]:
df_.shape

(212, 3)

## Bulid Location Mapping


In [93]:
#load geo_data
geo_df = pd.read_csv("http://cocl.us/Geospatial_data")
geo_df.columns=["Postcode","Latitude","Longitude"]
geo_df.head()

Postcode   Latitude  Longitude
0      M1B  43.806686 -79.194353
1      M1C  43.784535 -79.160497
2      M1E  43.763573 -79.188711
3      M1G  43.770992 -79.216917
4      M1H  43.773136 -79.239476

In [94]:
#merge_data
df=pd.merge(df,geo_df,on="Postcode")
df.head()

Postcode           Borough     Neighbourhood   Latitude  Longitude
0      M3A        North York         Parkwoods  43.753259 -79.329656
1      M4A        North York  Victoria Village  43.725882 -79.315572
2      M5A  Downtown Toronto      Harbourfront  43.654260 -79.360636
3      M5A  Downtown Toronto       Regent Park  43.654260 -79.360636
4      M6A        North York  Lawrence Heights  43.718518 -79.464763

In [95]:
#arrage to mapping
df_geo=df[["Borough","Neighbourhood","Latitude","Longitude"]]
df_geo.head()

Borough     Neighbourhood   Latitude  Longitude
0        North York         Parkwoods  43.753259 -79.329656
1        North York  Victoria Village  43.725882 -79.315572
2  Downtown Toronto      Harbourfront  43.654260 -79.360636
3  Downtown Toronto       Regent Park  43.654260 -79.360636
4        North York  Lawrence Heights  43.718518 -79.464763

In [96]:
address = 'Toronto, ON'
geolocator = Nominatim(user_agent='eiei')
location = geolocator.geocode(address)
Latitude = location.latitude
Longitude = location.longitude
print('The geograpical coordinates of Toronto are {}, {}.'.format(Latitude, Longitude))

The geograpical coordinates of Toronto are 43.653963, -79.387207.


## Map

In [97]:
# create map of Toronto using latitude and longitude values
map_toronto = folium.Map(location=[Latitude, Longitude], zoom_start=10)
# add markers to map
for lat, lng, borough, neighbourhood in zip(df['Latitude'], df['Longitude'], df['Borough'], df['Neighbourhood']):
    label = '{}, {}'.format(df_geo, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7).add_to(map_toronto)  
    
map_toronto

In [98]:
df['Borough'].value_counts()

Etobicoke           45
North York          38
Scarborough         38
Downtown Toronto    37
Central Toronto     17
West Toronto        13
York                 9
East Toronto         7
East York            6
Queen's Park         1
Mississauga          1
Name: Borough, dtype: int64

In [100]:
df_down=df[df['Borough']=='Downtown Toronto'].reset_index(drop=True)
df_down.head()

Postcode           Borough    Neighbourhood   Latitude  Longitude
0      M5A  Downtown Toronto     Harbourfront  43.654260 -79.360636
1      M5A  Downtown Toronto      Regent Park  43.654260 -79.360636
2      M5B  Downtown Toronto          Ryerson  43.657162 -79.378937
3      M5B  Downtown Toronto  Garden District  43.657162 -79.378937
4      M5C  Downtown Toronto   St. James Town  43.651494 -79.375418

## Map

In [101]:
address = 'Downtown Toronto, ON'
geolocator = Nominatim(user_agent='eiei')
location = geolocator.geocode(address)
Latitude = location.latitude
Longitude = location.longitude
print('The geograpical coordinates of Toronto are {}, {}.'.format(Latitude, Longitude))
# create map of Toronto using latitude and longitude values
map_Downtown_Toronto = folium.Map(location=[Latitude, Longitude], zoom_start=13)

# add markers to map
for lat, lng, borough, neighbourhood in zip(df_down['Latitude'], df_down['Longitude'], df_down['Borough'], df_down['Neighbourhood']):
    label = '{}, {}'.format(df_down, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7).add_to(map_Downtown_Toronto)  
    
map_Downtown_Toronto

The geograpical coordinates of Toronto are 43.655115, -79.380219.


## Foursquare API


In [102]:
CLIENT_ID = 'KBBBEGMEZTOHSSZEZW4D242ZT5OLJWIXB5323KISCTU2WYKR' #Foursquare ID
CLIENT_SECRET = 'BPTVHXOEY0GYMT3WCX3NSTTX4LBQSJKHDT5BWUAMAQQ43QWC' # Foursquare Secret
VERSION = '20180602' 

In [103]:
df_down['Neighbourhood'][0]

'Harbourfront'

In [104]:
neighborhood_latitude = df_down['Latitude'][0] 
neighborhood_longitude = df_down['Longitude'][0] 

In [105]:
LIMIT = 100   
radius = 5000
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighborhood_latitude, 
    neighborhood_longitude, 
    radius, 
    LIMIT)
url

'https://api.foursquare.com/v2/venues/explore?&client_id=KBBBEGMEZTOHSSZEZW4D242ZT5OLJWIXB5323KISCTU2WYKR&client_secret=BPTVHXOEY0GYMT3WCX3NSTTX4LBQSJKHDT5BWUAMAQQ43QWC&v=20180602&ll=43.6542599,-79.3606359&radius=5000&limit=100'

In [106]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5bda7c4fdb04f50a0908f6cc'},
 'response': {'groups': [{'items': [{'reasons': {'count': 0,
       'items': [{'reasonName': 'globalInteractionReason',
         'summary': 'This spot is popular',
         'type': 'general'}]},
      'referralId': 'e-0-54ea41ad498e9a11e9e13308-0',
      'venue': {'categories': [{'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/bakery_',
          'suffix': '.png'},
         'id': '4bf58dd8d48988d16a941735',
         'name': 'Bakery',
         'pluralName': 'Bakeries',
         'primary': True,
         'shortName': 'Bakery'}],
       'id': '54ea41ad498e9a11e9e13308',
       'location': {'address': '362 King St E',
        'cc': 'CA',
        'city': 'Toronto',
        'country': 'Canada',
        'crossStreet': 'Trinity St',
        'distance': 143,
        'formattedAddress': ['362 King St E (Trinity St)',
         'Toronto ON M5A 1K9',
         'Canada'],
        'labeledLatLngs': [{'label': 'display',
 

In [107]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [108]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

name      categories        lat        lng
0                  Roselle Desserts          Bakery  43.653447 -79.362017
1  The Distillery Historic District   Historic Site  43.650244 -79.359323
2          Distillery Sunday Market  Farmers Market  43.650075 -79.361832
3                     Tandem Coffee     Coffee Shop  43.653559 -79.361809
4                    Rooster Coffee     Coffee Shop  43.651900 -79.365609

In [109]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

100 venues were returned by Foursquare.


In [110]:
nearby_venues.shape

(100, 4)

In [111]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [38]:
downtown_venues = getNearbyVenues(names=df_down['Neighbourhood'],
                                   latitudes=df_down['Latitude'],
                                   longitudes=df_down['Longitude']
                                  )

Harbourfront
Regent Park
Ryerson
Garden District
St. James Town
Berczy Park
Central Bay Street
Christie
Adelaide
King
Richmond
Harbourfront East
Toronto Islands
Union Station
Design Exchange
Toronto Dominion Centre
Commerce Court
Victoria Hotel
Harbord
University of Toronto
Chinatown
Grange Park
Kensington Market
CN Tower
Bathurst Quay
Island airport
Harbourfront West
King and Spadina
Railway Lands
South Niagara
Rosedale
Stn A PO Boxes 25 The Esplanade
Cabbagetown
St. James Town
First Canadian Place
Underground city
Church and Wellesley


In [112]:
print(downtown_venues.shape)
downtown_venues.head()

(2494, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  Harbourfront               43.65426              -79.360636   
1  Harbourfront               43.65426              -79.360636   
2  Harbourfront               43.65426              -79.360636   
3  Harbourfront               43.65426              -79.360636   
4  Harbourfront               43.65426              -79.360636   

                 Venue  Venue Latitude  Venue Longitude        Venue Category  
0     Roselle Desserts       43.653447       -79.362017                Bakery  
1        Tandem Coffee       43.653559       -79.361809           Coffee Shop  
2  Body Blitz Spa East       43.654735       -79.359874                   Spa  
3   Morning Glory Cafe       43.653947       -79.361149        Breakfast Spot  
4      Cooper Koo YMCA       43.653191       -79.357947  Gym / Fitness Center

In [113]:
print('There are {} uniques categories.'.format(len(downtown_venues['Venue Category'].unique())))

There are 203 uniques categories.


In [41]:
#one hot encoding
downtown_onehot = pd.get_dummies(downtown_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
downtown_onehot['Neighborhood'] = downtown_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [downtown_onehot.columns[-1]] + list(downtown_onehot.columns[:-1])
downtown_onehot = downtown_onehot[fixed_columns]

print(downtown_onehot.shape)
downtown_onehot.head()

(2494, 203)


Yoga Studio  Accessories Store  Adult Boutique  Afghan Restaurant  Airport  \
0            0                  0               0                  0        0   
1            0                  0               0                  0        0   
2            0                  0               0                  0        0   
3            0                  0               0                  0        0   
4            0                  0               0                  0        0   

   Airport Food Court  Airport Gate  Airport Lounge  Airport Service  \
0                   0             0               0                0   
1                   0             0               0                0   
2                   0             0               0                0   
3                   0             0               0                0   
4                   0             0               0                0   

   Airport Terminal  American Restaurant  Antique Shop  Aquarium  \
0                 0                    0             0         0   
1                 0                    0             0         0   
2                 0                    0             0         0   
3                 0                    0             0         0   
4                 0                    0             0         0   

   Arepa Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0                 0            0           0                    0   
1                 0            0           0                    0   
2                 0            0           0                    0   
3                 0            0           0                    0   
4                 0            0           0                    0   

   Asian Restaurant  Athletics & Sports  BBQ Joint  Baby Store  Bagel Shop  \
0                 0                   0          0           0           0   
1                 0                   0          0           0           0   
2                 0                   0          0           0           0   
3                 0                   0          0           0           0   
4                 0                   0          0           0           0   

   Bakery  Bank  Bar  Baseball Stadium  Basketball Stadium  Beach  Beer Bar  \
0       1     0    0                 0                   0      0         0   
1       0     0    0                 0                   0      0         0   
2       0     0    0                 0                   0      0         0   
3       0     0    0                 0                   0      0         0   
4       0     0    0                 0                   0      0         0   

   Beer Store  Belgian Restaurant  Bistro  Boat or Ferry  Bookstore  \
0           0                   0       0              0          0   
1           0                   0       0              0          0   
2           0                   0       0              0          0   
3           0                   0       0              0          0   
4           0                   0       0              0          0   

   Brazilian Restaurant  Breakfast Spot  Brewery  Bubble Tea Shop  Building  \
0                     0               0        0                0         0   
1                     0               0        0                0         0   
2                     0               0        0                0         0   
3                     0               1        0                0         0   
4                     0               0        0                0         0   

   Burger Joint  Burrito Place  Butcher  Café  Caribbean Restaurant  \
0             0              0        0     0                     0   
1             0              0        0     0                     0   
2             0              0        0     0                     0   
3             0              0        0     0                     0   
4             0              0        0     0             

In [114]:
downtown_grouped = downtown_onehot.groupby('Neighborhood').mean().reset_index()
print(downtown_grouped.shape)
downtown_grouped.head()

(36, 203)


Neighborhood  Yoga Studio  Accessories Store  Adult Boutique  \
0       Adelaide          0.0               0.01             0.0   
1  Bathurst Quay          0.0               0.00             0.0   
2    Berczy Park          0.0               0.00             0.0   
3       CN Tower          0.0               0.00             0.0   
4    Cabbagetown          0.0               0.00             0.0   

   Afghan Restaurant   Airport  Airport Food Court  Airport Gate  \
0                0.0  0.000000            0.000000      0.000000   
1                0.0  0.076923            0.076923      0.076923   
2                0.0  0.000000            0.000000      0.000000   
3                0.0  0.076923            0.076923      0.076923   
4                0.0  0.000000            0.000000      0.000000   

   Airport Lounge  Airport Service  Airport Terminal  American Restaurant  \
0        0.000000         0.000000          0.000000                 0.04   
1        0.153846         0.153846          0.153846                 0.00   
2        0.000000         0.000000          0.000000                 0.00   
3        0.153846         0.153846          0.153846                 0.00   
4        0.000000         0.000000          0.000000                 0.00   

   Antique Shop  Aquarium  Arepa Restaurant  Art Gallery  Art Museum  \
0           0.0       0.0               0.0     0.010000        0.01   
1           0.0       0.0               0.0     0.000000        0.00   
2           0.0       0.0               0.0     0.018182        0.00   
3           0.0       0.0               0.0     0.000000        0.00   
4           0.0       0.0               0.0     0.000000        0.00   

   Arts & Crafts Store  Asian Restaurant  Athletics & Sports  BBQ Joint  \
0                  0.0              0.02                 0.0        0.0   
1                  0.0              0.00                 0.0        0.0   
2                  0.0              0.00                 0.0        0.0   
3                  0.0              0.00                 0.0        0.0   
4                  0.0              0.00                 0.0        0.0   

   Baby Store  Bagel Shop    Bakery      Bank   Bar  Baseball Stadium  \
0         0.0    0.000000  0.020000  0.000000  0.03               0.0   
1         0.0    0.000000  0.000000  0.000000  0.00               0.0   
2         0.0    0.018182  0.036364  0.000000  0.00               0.0   
3         0.0    0.000000  0.000000  0.000000  0.00               0.0   
4         0.0    0.000000  0.040816  0.020408  0.00               0.0   

   Basketball Stadium     Beach  Beer Bar  Beer Store  Belgian Restaurant  \
0            0.000000  0.000000  0.000000    0.000000            0.000000   
1            0.000000  0.000000  0.000000    0.000000            0.000000   
2            0.018182  0.018182  0.036364    0.000000            0.018182   
3            0.000000  0.000000  0.000000    0.000000            0.000000   
4            0.000000  0.000000  0.000000    0.020408            0.000000   

     Bistro  Boat or Ferry  Bookstore  Brazilian Restaurant  Breakfast Spot  \
0  0.000000       0.000000       0.01                  0.01        0.020000   
1  0.000000       0.076923       0.00                  0.00        0.000000   
2  0.018182       0.000000       0.00                  0.00        0.000000   
3  0.000000       0.076923       0.00                  0.00        0.000000   
4  0.000000       0.000000       0.00                  0.00        0.020408   

   Brewery  Bubble Tea Shop  Building  Burger Joint  Burrito Place   Butcher  \
0      0.0              0.0       0.0      0.020000           0.01  0.000000   
1      0.0              0.0       0.0      0.000000           0.00  0.000000   
2      0.0              0.0       0.0      0.018182           0.00  0.000000   
3      0.0              0.0       0.0      0.000000           0.00  0.000000   
4      0.0              0.0       0.0      0.000000           

In [115]:
num_top_venues = 5

for hood in downtown_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = downtown_grouped[downtown_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Adelaide----
                 venue  freq
0          Coffee Shop  0.07
1                 Café  0.06
2           Steakhouse  0.04
3  American Restaurant  0.04
4      Thai Restaurant  0.04


----Bathurst Quay----
              venue  freq
0    Airport Lounge  0.15
1   Airport Service  0.15
2  Airport Terminal  0.15
3             Plane  0.08
4           Airport  0.08


----Berczy Park----
                venue  freq
0         Coffee Shop  0.09
1        Cocktail Bar  0.05
2  Seafood Restaurant  0.04
3            Beer Bar  0.04
4                Café  0.04


----CN Tower----
              venue  freq
0    Airport Lounge  0.15
1   Airport Service  0.15
2  Airport Terminal  0.15
3             Plane  0.08
4           Airport  0.08


----Cabbagetown----
               venue  freq
0        Coffee Shop  0.08
1         Restaurant  0.08
2        Pizza Place  0.06
3  Indian Restaurant  0.04
4             Bakery  0.04


----Central Bay Street----
                 venue  freq
0          Coffee Shop

In [122]:

def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [123]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = downtown_grouped['Neighborhood']

for ind in np.arange(downtown_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(downtown_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0       Adelaide           Coffee Shop                  Café   
1  Bathurst Quay      Airport Terminal       Airport Service   
2    Berczy Park           Coffee Shop          Cocktail Bar   
3       CN Tower      Airport Terminal       Airport Service   
4    Cabbagetown           Coffee Shop            Restaurant   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0            Steakhouse       Thai Restaurant   American Restaurant   
1        Airport Lounge       Harbor / Marina          Airport Gate   
2        Farmers Market                Bakery           Cheese Shop   
3        Airport Lounge       Harbor / Marina          Airport Gate   
4           Pizza Place                Bakery                  Park   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0                   Gym            Restaurant                 Hotel   
1         Boat or Ferry                 Plane      Sculpture Garden   
2            Steakhouse                  Café            Restaurant   
3         Boat or Ferry                 Plane      Sculpture Garden   
4     Indian Restaurant                  Café             Pet Store   

  9th Most Common Venue 10th Most Common Venue  
0        Cosmetics Shop                    Bar  
1    Airport Food Court                Airport  
2    Seafood Restaurant               Beer Bar  
3    Airport Food Court                Airport  
4    Italian Restaurant                    Pub

#K-Cluster

In [151]:
# set number of clusters
kclusters = 5

downtown_grouped_clustering = downtown_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(downtown_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:37]

array([2, 1, 2, 1, 2, 0, 2, 4, 2, 0, 0, 0, 2, 2, 2, 0, 0, 1, 1, 2, 2, 1,
       1, 0, 2, 3, 2, 1, 2, 2, 0, 0, 0, 0, 2, 0], dtype=int32)

In [118]:
df_down.shape

(37, 5)

In [152]:
kmeans.labels_.shape

(36,)

In [155]:
downtown_merged = df_down.drop(df_down.index[len(df_down)-1])
downtown_merged.shape

(36, 6)

In [156]:


# add clustering labels
downtown_merged['Cluster Labels'] = kmeans.labels_


In [157]:

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
downtown_merged = downtown_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighbourhood')
downtown_merged.head(10) # check the last columns!

Postcode           Borough       Neighbourhood   Latitude  Longitude  \
0      M5A  Downtown Toronto        Harbourfront  43.654260 -79.360636   
1      M5A  Downtown Toronto         Regent Park  43.654260 -79.360636   
2      M5B  Downtown Toronto             Ryerson  43.657162 -79.378937   
3      M5B  Downtown Toronto     Garden District  43.657162 -79.378937   
4      M5C  Downtown Toronto      St. James Town  43.651494 -79.375418   
5      M5E  Downtown Toronto         Berczy Park  43.644771 -79.373306   
6      M5G  Downtown Toronto  Central Bay Street  43.657952 -79.387383   
7      M6G  Downtown Toronto            Christie  43.669542 -79.422564   
8      M5H  Downtown Toronto            Adelaide  43.650571 -79.384568   
9      M5H  Downtown Toronto                King  43.650571 -79.384568   

   Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
0               2           Coffee Shop                  Park   
1               1           Coffee Shop                  Park   
2               2           Coffee Shop        Clothing Store   
3               1           Coffee Shop        Clothing Store   
4               2           Coffee Shop            Restaurant   
5               0           Coffee Shop          Cocktail Bar   
6               2           Coffee Shop                  Café   
7               4         Grocery Store                  Café   
8               2           Coffee Shop                  Café   
9               0           Coffee Shop                  Café   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0                  Café                Bakery    Mexican Restaurant   
1                  Café                Bakery    Mexican Restaurant   
2        Cosmetics Shop                  Café                   Bar   
3        Cosmetics Shop                  Café                   Bar   
4                  Café                Bakery    Italian Restaurant   
5        Farmers Market                Bakery           Cheese Shop   
6    Italian Restaurant        Sandwich Place          Burger Joint   
7                  Park    Italian Restaurant    Athletics & Sports   
8            Steakhouse       Thai Restaurant   American Restaurant   
9            Steakhouse       Thai Restaurant   American Restaurant   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0        Breakfast Spot               Theater                   Pub   
1        Breakfast Spot               Theater                   Pub   
2   Japanese Restaurant       Bubble Tea Shop         Movie Theater   
3   Japanese Restaurant       Bubble Tea Shop         Movie Theater   
4        Clothing Store                  Park           Pizza Place   
5            Steakhouse                  Café            Restaurant   
6   Japanese Restaurant                   Bar       Bubble Tea Shop   
7                 Diner            Baby Store             Nightclub   
8                   Gym            Restaurant                 Hotel   
9                   Gym            Restaurant                 Hotel   

  9th Most Common Venue 10th Most Common Venue  
0  Gym / Fitness Center             Beer Store  
1  Gym / Fitness Center             Beer Store  
2           Pizza Place                  Diner  
3           Pizza Place                  Diner  
4             Gastropub                  Hotel  
5    Seafood Restaurant               Beer Bar  
6        Ice Cream Shop                    Spa  
7     Convenience Store            Coffee Shop  
8        Cosmetics Shop                    Bar  
9        Cosmetics Shop                    Bar

In [158]:
# create map
map_clusters = folium.Map(location=[Latitude, Longitude], zoom_start=14)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i+x+(i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(downtown_merged['Latitude'], downtown_merged['Longitude'], downtown_merged['Neighbourhood'], downtown_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

## Cluster Labels = 0

In [159]:
downtown_merged.loc[downtown_merged['Cluster Labels'] == 0, downtown_merged.columns[[1] + list(range(5, downtown_merged.shape[1]))]]


Borough  Cluster Labels 1st Most Common Venue  \
5   Downtown Toronto               0           Coffee Shop   
9   Downtown Toronto               0           Coffee Shop   
10  Downtown Toronto               0           Coffee Shop   
11  Downtown Toronto               0           Coffee Shop   
15  Downtown Toronto               0           Coffee Shop   
16  Downtown Toronto               0           Coffee Shop   
23  Downtown Toronto               0      Airport Terminal   
30  Downtown Toronto               0                  Park   
31  Downtown Toronto               0           Coffee Shop   
32  Downtown Toronto               0           Coffee Shop   
33  Downtown Toronto               0           Coffee Shop   
35  Downtown Toronto               0           Coffee Shop   

   2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
5           Cocktail Bar        Farmers Market                Bakery   
9                   Café            Steakhouse       Thai Restaurant   
10                  Café            Steakhouse       Thai Restaurant   
11                 Hotel           Pizza Place                  Café   
15                 Hotel                  Café   American Restaurant   
16                 Hotel                  Café            Restaurant   
23       Airport Service        Airport Lounge       Harbor / Marina   
30                 Trail            Playground         Women's Store   
31                  Café            Restaurant                 Hotel   
32            Restaurant           Pizza Place                Bakery   
33            Restaurant                  Café                Bakery   
35                  Café                 Hotel            Restaurant   

   5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
5            Cheese Shop            Steakhouse                  Café   
9    American Restaurant                   Gym            Restaurant   
10   American Restaurant                   Gym            Restaurant   
11              Aquarium               Brewery        Scenic Lookout   
15                   Gym            Sports Bar    Italian Restaurant   
16   American Restaurant    Italian Restaurant            Steakhouse   
23          Airport Gate         Boat or Ferry                 Plane   
30         Deli / Bodega   Dumpling Restaurant            Donut Shop   
31              Beer Bar    Seafood Restaurant          Cocktail Bar   
32                  Park     Indian Restaurant                  Café   
33    Italian Restaurant        Clothing Store                  Park   
35            Steakhouse                   Bar         Deli / Bodega   

   8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
5             Restaurant    Seafood Restaurant               Beer Bar  
9                  Hotel        Cosmetics Shop                    Bar  
10                 Hotel        Cosmetics Shop                    Bar  
11    Italian Restaurant            Sports Bar             Steakhouse  
15         Deli / Bodega            Restaurant              Gastropub  
16                   Gym    Seafood Restaurant          Deli / Bodega  
23      Sculpture Garden    Airport Food Court                Airport  
30      Doner Restaurant               Dog Run         Discount Store  
31                   Pub                Bakery           Burger Joint  
32             Pet Store    Italian Restaurant                    Pub  
33           Pizza Place             Gastropub                  Hotel  
35             Gastropub                   Gym    American Restaurant

## Cluster Labels = 1

In [160]:
downtown_merged.loc[downtown_merged['Cluster Labels'] == 1, downtown_merged.columns[[1] + list(range(5, downtown_merged.shape[1]))]]


Borough  Cluster Labels 1st Most Common Venue  \
1   Downtown Toronto               1           Coffee Shop   
3   Downtown Toronto               1           Coffee Shop   
17  Downtown Toronto               1           Coffee Shop   
18  Downtown Toronto               1                  Café   
21  Downtown Toronto               1                  Café   
22  Downtown Toronto               1                  Café   
27  Downtown Toronto               1      Airport Terminal   

            2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
1                            Park                  Café                Bakery   
3                  Clothing Store        Cosmetics Shop                  Café   
17                          Hotel                  Café            Restaurant   
18                      Bookstore                Bakery                   Bar   
21  Vegetarian / Vegan Restaurant    Chinese Restaurant                   Bar   
22  Vegetarian / Vegan Restaurant    Chinese Restaurant                   Bar   
27                Airport Service        Airport Lounge       Harbor / Marina   

   5th Most Common Venue  6th Most Common Venue 7th Most Common Venue  \
1     Mexican Restaurant         Breakfast Spot               Theater   
3                    Bar    Japanese Restaurant       Bubble Tea Shop   
17   American Restaurant     Italian Restaurant            Steakhouse   
18            Restaurant    Japanese Restaurant           Coffee Shop   
21    Mexican Restaurant  Vietnamese Restaurant                Bakery   
22    Mexican Restaurant  Vietnamese Restaurant                Bakery   
27          Airport Gate          Boat or Ferry                 Plane   

      8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
1                       Pub  Gym / Fitness Center             Beer Store  
3             Movie Theater           Pizza Place                  Diner  
17                      Gym    Seafood Restaurant          Deli / Bodega  
18  Comfort Food Restaurant         Poutine Place                    Pub  
21      Dumpling Restaurant           Coffee Shop            Gaming Cafe  
22      Dumpling Restaurant           Coffee Shop            Gaming Cafe  
27         Sculpture Garden    Airport Food Court                Airport

## Cluster Labels = 2

In [161]:
downtown_merged.loc[downtown_merged['Cluster Labels'] == 2, downtown_merged.columns[[1] + list(range(5, downtown_merged.shape[1]))]]


Borough  Cluster Labels 1st Most Common Venue  \
0   Downtown Toronto               2           Coffee Shop   
2   Downtown Toronto               2           Coffee Shop   
4   Downtown Toronto               2           Coffee Shop   
6   Downtown Toronto               2           Coffee Shop   
8   Downtown Toronto               2           Coffee Shop   
12  Downtown Toronto               2           Coffee Shop   
13  Downtown Toronto               2           Coffee Shop   
14  Downtown Toronto               2           Coffee Shop   
19  Downtown Toronto               2                  Café   
20  Downtown Toronto               2                  Café   
24  Downtown Toronto               2      Airport Terminal   
26  Downtown Toronto               2      Airport Terminal   
28  Downtown Toronto               2      Airport Terminal   
29  Downtown Toronto               2      Airport Terminal   
34  Downtown Toronto               2           Coffee Shop   

            2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0                            Park                  Café                Bakery   
2                  Clothing Store        Cosmetics Shop                  Café   
4                      Restaurant                  Café                Bakery   
6                            Café    Italian Restaurant        Sandwich Place   
8                            Café            Steakhouse       Thai Restaurant   
12                          Hotel           Pizza Place                  Café   
13                          Hotel           Pizza Place                  Café   
14                          Hotel                  Café   American Restaurant   
19                      Bookstore                Bakery                   Bar   
20  Vegetarian / Vegan Restaurant    Chinese Restaurant                   Bar   
24                Airport Service        Airport Lounge       Harbor / Marina   
26                Airport Service        Airport Lounge       Harbor / Marina   
28                Airport Service        Airport Lounge       Harbor / Marina   
29                Airport Service        Airport Lounge       Harbor / Marina   
34                           Café                 Hotel            Restaurant   

   5th Most Common Venue  6th Most Common Venue 7th Most Common Venue  \
0     Mexican Restaurant         Breakfast Spot               Theater   
2                    Bar    Japanese Restaurant       Bubble Tea Shop   
4     Italian Restaurant         Clothing Store                  Park   
6           Burger Joint    Japanese Restaurant                   Bar   
8    American Restaurant                    Gym            Restaurant   
12              Aquarium                Brewery        Scenic Lookout   
13              Aquarium                Brewery        Scenic Lookout   
14                   Gym             Sports Bar    Italian Restaurant   
19            Restaurant    Japanese Restaurant           Coffee Shop   
20    Mexican Restaurant  Vietnamese Restaurant                Bakery   
24          Airport Gate          Boat or Ferry                 Plane   
26          Airport Gate          Boat or Ferry                 Plane   
28          Airport Gate          Boat or Ferry                 Plane   
29          Airport Gate          Boat or Ferry                 Plane   
34            Steakhouse                    Bar         Deli / Bodega   

      8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
0                       Pub  Gym / Fitness Center             Beer Store  
2             Movie Theater           Pizza Place                  Diner  
4               Pizza Place             Gastropub                  Hotel  
6           Bubble Tea Shop        Ice Cream Shop                    Spa  
8                     Hotel        Cosmetics Shop                    Bar  
12       Italian Restaurant            Sports Bar             Steakhouse  
13       Italian Restaurant  

## Cluster Labels = 3

In [162]:
downtown_merged.loc[downtown_merged['Cluster Labels'] == 3, downtown_merged.columns[[1] + list(range(5, downtown_merged.shape[1]))]]


Borough  Cluster Labels 1st Most Common Venue  \
25  Downtown Toronto               3      Airport Terminal   

   2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
25       Airport Service        Airport Lounge       Harbor / Marina   

   5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
25          Airport Gate         Boat or Ferry                 Plane   

   8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
25      Sculpture Garden    Airport Food Court                Airport

## Cluster Labels = 4

In [163]:
downtown_merged.loc[downtown_merged['Cluster Labels'] == 4, downtown_merged.columns[[1] + list(range(5, downtown_merged.shape[1]))]]


Borough  Cluster Labels 1st Most Common Venue  \
7  Downtown Toronto               4         Grocery Store   

  2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
7                  Café                  Park    Italian Restaurant   

  5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
7    Athletics & Sports                 Diner            Baby Store   

  8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
7             Nightclub     Convenience Store            Coffee Shop